In [ ]:
import numpy as np
from sklearn.svm import SVR
from sklearn.metrics import mean_squared_error, r2_score

# Initialize Population
def initialize_population(pop_size, param_bounds):
    population = []
    for _ in range(pop_size):
        C = np.random.uniform(param_bounds['C'][0], param_bounds['C'][1])
        epsilon = np.random.uniform(param_bounds['epsilon'][0], param_bounds['epsilon'][1])
        gamma = np.random.uniform(param_bounds['gamma'][0], param_bounds['gamma'][1])
        population.append((C, epsilon, gamma))
    return population

# Evaluate Fitness
def evaluate_fitness(params, X_train, y_train, X_test, y_test):
    C, epsilon, gamma = params
    model = SVR(C=C, epsilon=epsilon, gamma=gamma)
    model.fit(X_train, y_train)
    predictions = model.predict(X_test)
    rmse = np.sqrt(mean_squared_error(y_test, predictions))
    return rmse

# Bald Eagle Optimizer (BES) Phase
def bes_phase(population, fitness_scores, global_best, param_bounds):
    new_population = []
    for i, (params, fitness) in enumerate(zip(population, fitness_scores)):
        C, epsilon, gamma = params
        r1, r2 = np.random.rand(), np.random.rand()
        new_C = C + r1 * (global_best[0] - C) + r2 * (np.mean([p[0] for p in population]) - C)
        new_epsilon = epsilon + r1 * (global_best[1] - epsilon) + r2 * (np.mean([p[1] for p in population]) - epsilon)
        new_gamma = gamma + r1 * (global_best[2] - gamma) + r2 * (np.mean([p[2] for p in population]) - gamma)
        new_population.append((
            np.clip(new_C, param_bounds['C'][0], param_bounds['C'][1]),
            np.clip(new_epsilon, param_bounds['epsilon'][0], param_bounds['epsilon'][1]),
            np.clip(new_gamma, param_bounds['gamma'][0], param_bounds['gamma'][1])
        ))
    return new_population

# Chimp Optimizer (CO) Phase
def co_phase(population, fitness_scores, global_best, param_bounds):
    new_population = []
    for i, (params, fitness) in enumerate(zip(population, fitness_scores)):
        C, epsilon, gamma = params
        w, c1, c2 = 0.5, np.random.rand(), np.random.rand()
        group_best = np.mean(population, axis=0)
        new_C = w * C + c1 * (global_best[0] - C) + c2 * (group_best[0] - C)
        new_epsilon = w * epsilon + c1 * (global_best[1] - epsilon) + c2 * (group_best[1] - epsilon)
        new_gamma = w * gamma + c1 * (global_best[2] - gamma) + c2 * (group_best[2] - gamma)
        new_population.append((
            np.clip(new_C, param_bounds['C'][0], param_bounds['C'][1]),
            np.clip(new_epsilon, param_bounds['epsilon'][0], param_bounds['epsilon'][1]),
            np.clip(new_gamma, param_bounds['gamma'][0], param_bounds['gamma'][1])
        ))
    return new_population

# Main Hybrid Optimization Process
def hybrid_optimization(X_train, y_train, X_test, y_test, param_bounds, pop_size=50, max_iter=100):
    population = initialize_population(pop_size, param_bounds)
    fitness_scores = [evaluate_fitness(params, X_train, y_train, X_test, y_test) for params in population]
    global_best = population[np.argmin(fitness_scores)]

    for _ in range(max_iter):
        population = bes_phase(population, fitness_scores, global_best, param_bounds)
        fitness_scores = [evaluate_fitness(params, X_train, y_train, X_test, y_test) for params in population]
        global_best = population[np.argmin(fitness_scores)]

        population = co_phase(population, fitness_scores, global_best, param_bounds)
        fitness_scores = [evaluate_fitness(params, X_train, y_train, X_test, y_test) for params in population]
        global_best = population[np.argmin(fitness_scores)]

    return global_best

# Example Usage
if __name__ == "__main__":
    from sklearn.model_selection import train_test_split
    from sklearn.datasets import make_regression

    # Generate synthetic data
    X, y = make_regression(n_samples=1000, n_features=10, noise=0.1)
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

    # Parameter bounds
    param_bounds = {
        'C': [1, 10000],
        'epsilon': [0.001, 1],
        'gamma': [0.01, 20]
    }

    # Run hybrid optimization
    best_params = hybrid_optimization(X_train, y_train, X_test, y_test, param_bounds)
    print("Best Parameters:", best_params)

    # Evaluate final model
    final_model = SVR(C=best_params[0], epsilon=best_params[1], gamma=best_params[2])
    final_model.fit(X_train, y_train)
    final_predictions = final_model.predict(X_test)
    final_rmse = np.sqrt(mean_squared_error(y_test, final_predictions))
    final_r2 = r2_score(y_test, final_predictions)
    print("Final RMSE:", final_rmse)
    print("Final R²:", final_r2)


In [ ]:
import numpy as np
from sklearn.svm import SVR
from sklearn.metrics import mean_squared_error, r2_score
from sklearn.model_selection import train_test_split
from sklearn.datasets import make_regression

# Hypothetical imports for optimization algorithms (replace with actual implementations)
# from ffa import FireflyAlgorithm
# from grey_wolf_optimizer import GreyWolfOptimizer
# from bes import BaldEagleSearch

# Evaluate Fitness
def evaluate_fitness(params, X_train, y_train, X_test, y_test):
    C, epsilon, gamma = params
    model = SVR(C=C, epsilon=epsilon, gamma=gamma)
    model.fit(X_train, y_train)
    predictions = model.predict(X_test)
    rmse = np.sqrt(mean_squared_error(y_test, predictions))
    return rmse

# Firefly Algorithm for SVR-FFA
def optimize_with_ffa(X_train, y_train, X_test, y_test, param_bounds, pop_size=50, max_iter=100):
    # Initialize Firefly Algorithm with bounds and population size
    ffa = FireflyAlgorithm(param_bounds, pop_size, max_iter)
    best_params = ffa.optimize(lambda params: evaluate_fitness(params, X_train, y_train, X_test, y_test))
    return best_params

# Grey Wolf Optimization for SVR-GWO
def optimize_with_gwo(X_train, y_train, X_test, y_test, param_bounds, pop_size=50, max_iter=100):
    # Initialize Grey Wolf Optimizer with bounds and population size
    gwo = GreyWolfOptimizer(param_bounds, pop_size, max_iter)
    best_params = gwo.optimize(lambda params: evaluate_fitness(params, X_train, y_train, X_test, y_test))
    return best_params

# Bald Eagle Search for SVR-BES
def optimize_with_bes(X_train, y_train, X_test, y_test, param_bounds, pop_size=50, max_iter=100):
    # Initialize Bald Eagle Search with bounds and population size
    bes = BaldEagleSearch(param_bounds, pop_size, max_iter)
    best_params = bes.optimize(lambda params: evaluate_fitness(params, X_train, y_train, X_test, y_test))
    return best_params

# Example Usage
if __name__ == "__main__":
    # Generate synthetic data
    X, y = make_regression(n_samples=1000, n_features=10, noise=0.1)
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

    # Parameter bounds
    param_bounds = {
        'C': [1, 10000],
        'epsilon': [0.001, 1],
        'gamma': [0.01, 20]
    }

    # SVR-FFA
    best_params_ffa = optimize_with_ffa(X_train, y_train, X_test, y_test, param_bounds)
    print("Best Parameters for SVR-FFA:", best_params_ffa)
    final_model_ffa = SVR(C=best_params_ffa[0], epsilon=best_params_ffa[1], gamma=best_params_ffa[2])
    final_model_ffa.fit(X_train, y_train)
    predictions_ffa = final_model_ffa.predict(X_test)
    print("SVR-FFA RMSE:", np.sqrt(mean_squared_error(y_test, predictions_ffa)))
    print("SVR-FFA R²:", r2_score(y_test, predictions_ffa))

    # SVR-GWO
    best_params_gwo = optimize_with_gwo(X_train, y_train, X_test, y_test, param_bounds)
    print("Best Parameters for SVR-GWO:", best_params_gwo)
    final_model_gwo = SVR(C=best_params_gwo[0], epsilon=best_params_gwo[1], gamma=best_params_gwo[2])
    final_model_gwo.fit(X_train, y_train)
    predictions_gwo = final_model_gwo.predict(X_test)
    print("SVR-GWO RMSE:", np.sqrt(mean_squared_error(y_test, predictions_gwo)))
    print("SVR-GWO R²:", r2_score(y_test, predictions_gwo))

    # SVR-BES
    best_params_bes = optimize_with_bes(X_train, y_train, X_test, y_test, param_bounds)
    print("Best Parameters for SVR-BES:", best_params_bes)
    final_model_bes = SVR(C=best_params_bes[0], epsilon=best_params_bes[1], gamma=best_params_bes[2])
    final_model_bes.fit(X_train, y_train)
    predictions_bes = final_model_bes.predict(X_test)
    print("SVR-BES RMSE:", np.sqrt(mean_squared_error(y_test, predictions_bes)))
    print("SVR-BES R²:", r2_score(y_test, predictions_bes))
